In [1]:
import pandas as pd 
import math
import re
import mysql.connector


In [28]:
data = pd.read_csv("barcelona_listings.csv") 
    
data.head()

id                         listing_url  \
0  18666  https://www.airbnb.com/rooms/18666   
1  18674  https://www.airbnb.com/rooms/18674   
2  21605  https://www.airbnb.com/rooms/21605   
3  25786  https://www.airbnb.com/rooms/25786   
4  31377  https://www.airbnb.com/rooms/31377   

                                              name  \
0                          Flat with Sunny Terrace   
1  Huge flat for 8 people close to Sagrada Familia   
2                        Nice and sunny duble room   
3       NICE ROOM AVAILABLE IN THE HEART OF GRACIA   
4                      Room for 2,  Sagrada Famili   

                                             summary  \
0  Apartment located near the "Plaza de las Glori...   
1  110m2 apartment to rent in Barcelona. Located ...   
2  The flat is in Poblenou district, and the room...   
3  JUST GO THROUGH THE MANY REVIEWS I GOT THROUGH...   
4  The room in 500 m from Sagrada Familia. 3 bran...   

                                               space  \
0  Nice apartment situated on the penthouse floor...   
1  Apartment with 110 m2 located in the 6th floor...   
2  L'apartament està al barri de Poblenou, i l'ha...   
3  Room available for rent.-  PEDRO PEREZ.  Share...   
4  Great location, right next to Sagrada Familia,...   

                                         description  \
0  Apartment located near the "Plaza de las Glori...   
1  110m2 apartment to rent in Barcelona. Located ...   
2  The flat is in Poblenou district, and the room...   
3  JUST GO THROUGH THE MANY REVIEWS I GOT THROUGH...   
4  The room in 500 m from Sagrada Familia. 3 bran...   

                               neighborhood_overview  \
0  Apartment in Barcelona near to the Plaza de la...   
1  Apartment in Barcelona located in the heart of...   
2  Poblenou as one of the few areas that has grow...   
3  Solo decir que a menudo ni salgo del barrio. M...   
4                                                NaN   

                                               notes  \
0                                                NaN   
1                                                NaN   
2  Tingues en compte que vivim amb gats, assegura...   
3  No dudes en perdir una cita para un masaje rel...   
4                                                NaN   

                                             transit  \
0  Good transports connections, 50 m from the met...   
1  Good transport connection,  150 m from metro “...   
2  By metro, tram, bus, taxi, bicycle. See more i...   
3  Metro con las principales estaciones. A pie. E...   
4  From airport L9 to st. Collblanc. From Collbla...   

                                              access  \
0  Free Wifi - air conditioning. We will provide ...   
1  Free Wifi - air conditioning. We will provide ...   
2  The kitchen is fully equipped and can use the ...   
3  All access with respect. Kitchen facilities ne...   
4                                                NaN   

                ...                review_scores_accuracy  \
0               ...                                  10.0   
1               ...                                   9.0   
2               ...                                   9.0   
3               ...                                   9.0   
4               ...                                   9.0   

  review_scores_cleanliness review_scores_checkin  \
0                      10.0                   2.0   
1                      10.0                  10.0   
2                       9.0                  10.0   
3                       9.0                  10.0   
4                      10.0                  10.0   

   review_scores_communication review_scores_location review_scores_value  \
0                         10.0                   10.0                 8.0   
1                         10.0                    9.0                 9.0   
2                         10.0                    9.0                 9.0   
3                         10.0         

In [60]:
HOST = "cs322-db.epfl.ch"
PORT = 1521
USER = "C##DB2019_G11"
PASSWORD = " DB2019_G11"
SID = "ORCLCDB"

#cnx = mysql.connector.connect(user=USER, password=PASSWORD,
 #                             host=HOST,
 #                             port=PORT)
#cursor = cnx.cursor()
#cursor.execute("USE AIRBNB")
#cursor.execute("SELECT * FROM Listing")

In [10]:
def concat_file(files):
    lfs = []
    for path in files:
        lfs.append(pd.read_csv(path, skipinitialspace=True, nrows=500))
    return pd.concat(lfs)

In [57]:
listingsFiles = ["barcelona_listings.csv","berlin_listings_filtered.csv","madrid_listings_filtered.csv"]
listings = concat_file(listingsFiles).rename(columns={
    'host_id':'user_id',
    'host_name':'user_name'})

In [11]:
calendarFiles = ["barcelona_calendar.csv","berlin_calendar.csv","madrid_calendar.csv"]
calendars = concat_file(calendarFiles)

In [60]:
reviewsFiles = ["barcelona_reviews.csv","berlin_reviews.csv","madrid_reviews.csv"]
reviews = concat_file(reviewsFiles).rename(columns={
    'reviewer_id':'user_id',
    'reviewer_name':'user_name'})

In [59]:
users = []
users.append(reviews[['user_id', 'user_name']])
users.append(listings[['user_id', 'user_name']])
users = pd.concat(users).drop_duplicates()
tmp.head(3)

user_id    user_name
0   1559265         Jody
1   4841196        Caron
2  11600277  Juan Carlos

In [6]:
def price_handler(price):
    if(not isinstance(price, str)):
        return None
    else:
        return int(re.sub("[^0-9]", "", price))

In [5]:
def default(arg):
    if (isinstance(arg, str)):
        return arg[:4000]
    return arg

In [13]:
def rules_respected(attributes, rules , att_columns):
    temp = []
    for idx, att in enumerate(attributes):
        att = rules.get(att_columns[idx], default)(att)
        if att is None:
            return None
        temp.append(att)
    return tuple(temp)

In [15]:
def insert_values (df, att_columns, table_name, rules = {}):
    att_names = '(' + ', '.join(att_columns) + ')'
    att_nb = len(att_columns)
    att_type = '(' + ', '.join(["%s"] * att_nb) + ')'
    sql_insert_query = "INSERT INTO " + table_name + att_names + " VALUES " + att_type
    for attributes in df.values:
        attributes = rules_respected(attributes, rules, att_columns)
        if attributes is None:
            continue
        print(sql_insert_query + str(attributes))
        #cursor.execute(sql_insert_query, attributes)
        #connection.commit()

In [33]:
att_columns = ['neighbourhood', 'city', 'country_code', 'country']
insert_values(listings[att_columns], att_columns, "Neighbourhood")

INSERT INTO Neighbourhood(neighbourhood, city, country_code, country) VALUES (%s, %s, %s, %s)("El Camp de l'Arpa del Clot", 'Barcelona', 'ES', 'Spain')
INSERT INTO Neighbourhood(neighbourhood, city, country_code, country) VALUES (%s, %s, %s, %s)('La Sagrada Família', 'Barcelona', 'ES', 'Spain')
INSERT INTO Neighbourhood(neighbourhood, city, country_code, country) VALUES (%s, %s, %s, %s)('El Poblenou', 'Barcelona', 'ES', 'Spain')
INSERT INTO Neighbourhood(neighbourhood, city, country_code, country) VALUES (%s, %s, %s, %s)('Vila de Gràcia', 'Barcelona', 'ES', 'Spain')
INSERT INTO Neighbourhood(neighbourhood, city, country_code, country) VALUES (%s, %s, %s, %s)('El Baix Guinardó', 'Barcelona', 'ES', 'Spain')
INSERT INTO Neighbourhood(neighbourhood, city, country_code, country) VALUES (%s, %s, %s, %s)('El Baix Guinardó', 'Barcelona', 'ES', 'Spain')
INSERT INTO Neighbourhood(neighbourhood, city, country_code, country) VALUES (%s, %s, %s, %s)("La Nova Esquerra de l'Eixample", 'Barcelona', 'E

INSERT INTO Neighbourhood(neighbourhood, city, country_code, country) VALUES (%s, %s, %s, %s)('Embajadores', 'Madrid', 'ES', 'Spain')
INSERT INTO Neighbourhood(neighbourhood, city, country_code, country) VALUES (%s, %s, %s, %s)('Gaztambide', 'Madrid', 'ES', 'Spain')
INSERT INTO Neighbourhood(neighbourhood, city, country_code, country) VALUES (%s, %s, %s, %s)('Ciudad Lineal', 'Madrid', 'ES', 'Spain')
INSERT INTO Neighbourhood(neighbourhood, city, country_code, country) VALUES (%s, %s, %s, %s)('Puente de Vallecas', 'Madrid', 'ES', 'Spain')
INSERT INTO Neighbourhood(neighbourhood, city, country_code, country) VALUES (%s, %s, %s, %s)('Ciudad Lineal', 'Madrid', 'ES', 'Spain')
INSERT INTO Neighbourhood(neighbourhood, city, country_code, country) VALUES (%s, %s, %s, %s)('Sol', 'Madrid', 'ES', 'Spain')
INSERT INTO Neighbourhood(neighbourhood, city, country_code, country) VALUES (%s, %s, %s, %s)('Palacio', 'Madrid', 'ES', 'Spain')
INSERT INTO Neighbourhood(neighbourhood, city, country_code, cou

In [34]:
att_columns = ['id', 'neighbourhood', 'listing_url', 'name', 'summary', 'space']
insert_values(listings[att_columns], att_columns, "Listing")

INSERT INTO Listing(id, neighbourhood, listing_url, name, summary, space) VALUES (%s, %s, %s, %s, %s, %s)(18666, "El Camp de l'Arpa del Clot", 'https://www.airbnb.com/rooms/18666', 'Flat with Sunny Terrace', 'Apartment located near the "Plaza de las Glorias" and the second-hand market (Encants). The accommodation is also close to the National Theatre of Catalunya and the Agbar Tower which has become one of the new symbols of Barcelona.  Licence number: HUTB-(PHONE NUMBER HIDDEN)', 'Nice apartment situated on the penthouse floor of a building with elevator. Huge Living/dining-room with double sofa-bed  1 bedroom with two single beds  1 bedroom with double bed  Nice kitchen opened to the living/dining-room and fully equipped for 6 people  Bathroom with shower  The accommodation has been recently renovated and tastefully decorated with a comfortable furniture and wood floor. Also it is equipped with air-conditioning and heating.')
INSERT INTO Listing(id, neighbourhood, listing_url, name, 

INSERT INTO Listing(id, neighbourhood, listing_url, name, summary, space) VALUES (%s, %s, %s, %s, %s, %s)(716232, 'Ciudad Lineal', 'https://www.airbnb.com/rooms/716232', 'Loft near Metro - 75m2 - 5pax - 2wc', 'Cómodo apartamento con dos baños, cerca de la plaza de toros de Las Ventas. Con mercado, tiendas, bares y restaurantes cerca, y el Metro de Barrio de la Concepción a solo 200 metros. Totalmente equipado. Pueden dormir hasta un máximo de 5 personas.', 'Loft for rent in Madrid, surface 75 m2. Two bedrooms and two bathrooms. modern decoration, High ceilings, garden, close to Metro  station. Located at Barrio de la Concepción, close to Las Ventas Bull Ring. Quiet area, full of small shops,  a market and supermarkets, restaurants, coffe shops, etc. The nearest Metro Station (Bº Concepción – Line 7) is 100 m from the apartment. Different bus lines connect to the city centre. Cars can be parked in the street without payment. Easy access to M-30. One of the bedrooms has a double bed and 

In [18]:
att_columns = ['listing_id', 'date', 'available', 'price']
rules = {'price': price_handler}
insert_values(calendars[att_columns], att_columns, "calendar", rules = rules)

INSERT INTO calendar(listing_id, date, available, price) VALUES (%s, %s, %s, %s)(74562, '2019-11-06', 't', 6000)
INSERT INTO calendar(listing_id, date, available, price) VALUES (%s, %s, %s, %s)(74562, '2019-11-05', 't', 6000)
INSERT INTO calendar(listing_id, date, available, price) VALUES (%s, %s, %s, %s)(74562, '2019-11-04', 't', 6000)
INSERT INTO calendar(listing_id, date, available, price) VALUES (%s, %s, %s, %s)(74562, '2019-11-03', 't', 6000)
INSERT INTO calendar(listing_id, date, available, price) VALUES (%s, %s, %s, %s)(74562, '2019-11-02', 't', 6500)
INSERT INTO calendar(listing_id, date, available, price) VALUES (%s, %s, %s, %s)(74562, '2019-11-01', 't', 6500)
INSERT INTO calendar(listing_id, date, available, price) VALUES (%s, %s, %s, %s)(74562, '2019-10-31', 't', 6000)
INSERT INTO calendar(listing_id, date, available, price) VALUES (%s, %s, %s, %s)(74562, '2019-10-30', 't', 6000)
INSERT INTO calendar(listing_id, date, available, price) VALUES (%s, %s, %s, %s)(74562, '2019-10

In [35]:
att_columns = ['id', 'description', 'neighborhood_overview', 'notes', 'transit', 'access','interaction','house_rules','picture_url','latitude','longitude']
insert_values(listings[att_columns], att_columns, "Listing_descr")

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




INSERT INTO Listing_descr(id, description, neighborhood_overview, notes, transit, access, interaction, house_rules, picture_url, latitude, longitude) VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)(691598, "Private room in a bright flat in the center of Madrid, calle Mayor. The room is silence, wide and with a double bed and views to the city and the mountains. The flat has a nice living room with fire place and lounge space.  hight speed wifi Our house is cozy, with a fireplace in the living room. We are located in the sixth floor of the building (there is an elevator, of course). Every room has a window looking to a large courtyard, so the appartment is very quiet. There are views to the neighborhood's rooftops and the mountains, perfect for enjoying mornings and sunsets. The apartment has everything you need: * High speed Wi-Fi (fiber) * 2 bedrooms with double beds of 1.50 cm (linen included) * A living room with sofa, bookshelves and a desk, perfect for those who come to Madri

In [36]:
att_columns = ['id', 'property_type', 'room_type', 'accommodates', 'bathrooms', 'bedrooms','beds','bed_type','amenities','square_feet']
insert_values(listings[att_columns], att_columns, "Listing_detail")

INSERT INTO Listing_detail(id, property_type, room_type, accommodates, bathrooms, bedrooms, beds, bed_type, amenities, square_feet) VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s)(18666, 'Apartment', 'Entire home/apt', 6, 1.0, 2.0, 4.0, 'Real Bed', '{TV,Internet,Wifi,"Air conditioning","Wheelchair accessible",Kitchen,Elevator,"Free street parking",Heating,"Family/kid friendly",Washer,Dryer,Essentials,Shampoo,"Hair dryer","Hot water","Host greets you","Paid parking on premises"}', 75.0)
INSERT INTO Listing_detail(id, property_type, room_type, accommodates, bathrooms, bedrooms, beds, bed_type, amenities, square_feet) VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s)(18674, 'Apartment', 'Entire home/apt', 8, 2.0, 3.0, 6.0, 'Real Bed', '{TV,Internet,Wifi,"Air conditioning","Wheelchair accessible",Kitchen,Elevator,"Free street parking","Buzzer/wireless intercom",Heating,"Family/kid friendly",Washer,Essentials,Shampoo,Hangers,"Hair dryer",Iron,"Laptop friendly workspace",Crib,"Hot water","Host

INSERT INTO Listing_detail(id, property_type, room_type, accommodates, bathrooms, bedrooms, beds, bed_type, amenities, square_feet) VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s)(745664, 'Apartment', 'Private room', 2, 1.0, 1.0, 2.0, 'Real Bed', '{TV,Internet,Wifi,"Air conditioning","Paid parking off premises","Smoking allowed",Elevator,Heating,"Smoke detector","First aid kit",Essentials,Shampoo,"Lock on bedroom door","24-hour check-in",Hangers,"Hair dryer",Iron,"Laptop friendly workspace","Self check-in","Smart lock","Hot water"}', 8.0)
INSERT INTO Listing_detail(id, property_type, room_type, accommodates, bathrooms, bedrooms, beds, bed_type, amenities, square_feet) VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s)(745728, 'Serviced apartment', 'Entire home/apt', 12, 4.0, 4.0, 8.0, 'Real Bed', '{TV,Wifi,"Air conditioning","Wheelchair accessible",Kitchen,Elevator,Heating,"Family/kid friendly",Washer,Dryer,Essentials,Hangers,"Hair dryer",Iron,"Laptop friendly workspace",Bathtub,"Baby bat

In [38]:
att_columns = ['id', 'price', 'weekly_price', 'monthly_price', 'security_deposit', 'cleaning_fee','guests_included','extra_people']
insert_values(listings[att_columns], att_columns, "Listing_price")

INSERT INTO Listing_price(id, price, weekly_price, monthly_price, security_deposit, cleaning_fee, guests_included, extra_people) VALUES (%s, %s, %s, %s, %s, %s, %s, %s)(18666, '$130.00', nan, nan, '$150.00', '$42.00', 2, '$25.00')
INSERT INTO Listing_price(id, price, weekly_price, monthly_price, security_deposit, cleaning_fee, guests_included, extra_people) VALUES (%s, %s, %s, %s, %s, %s, %s, %s)(18674, '$60.00', nan, nan, '$150.00', '$50.00', 2, '$30.00')
INSERT INTO Listing_price(id, price, weekly_price, monthly_price, security_deposit, cleaning_fee, guests_included, extra_people) VALUES (%s, %s, %s, %s, %s, %s, %s, %s)(21605, '$33.00', nan, nan, '$100.00', nan, 1, '$10.00')
INSERT INTO Listing_price(id, price, weekly_price, monthly_price, security_deposit, cleaning_fee, guests_included, extra_people) VALUES (%s, %s, %s, %s, %s, %s, %s, %s)(25786, '$31.00', nan, nan, nan, nan, 1, '$31.00')
INSERT INTO Listing_price(id, price, weekly_price, monthly_price, security_deposit, cleaning_fe

In [39]:
att_columns = ['id', 'review_scores_rating', 'review_scores_accuracy', 'review_scores_cleanliness', 'review_scores_checkin', 'review_scores_communication','review_scores_location','review_scores_value']
insert_values(listings[att_columns], att_columns, "Listing_score")

INSERT INTO Listing_score(id, review_scores_rating, review_scores_accuracy, review_scores_cleanliness, review_scores_checkin, review_scores_communication, review_scores_location, review_scores_value) VALUES (%s, %s, %s, %s, %s, %s, %s, %s)(18666.0, 80.0, 10.0, 10.0, 2.0, 10.0, 10.0, 8.0)
INSERT INTO Listing_score(id, review_scores_rating, review_scores_accuracy, review_scores_cleanliness, review_scores_checkin, review_scores_communication, review_scores_location, review_scores_value) VALUES (%s, %s, %s, %s, %s, %s, %s, %s)(18674.0, 85.0, 9.0, 10.0, 10.0, 10.0, 9.0, 9.0)
INSERT INTO Listing_score(id, review_scores_rating, review_scores_accuracy, review_scores_cleanliness, review_scores_checkin, review_scores_communication, review_scores_location, review_scores_value) VALUES (%s, %s, %s, %s, %s, %s, %s, %s)(21605.0, 89.0, 9.0, 9.0, 10.0, 10.0, 9.0, 9.0)
INSERT INTO Listing_score(id, review_scores_rating, review_scores_accuracy, review_scores_cleanliness, review_scores_checkin, review_sco

INSERT INTO Listing_score(id, review_scores_rating, review_scores_accuracy, review_scores_cleanliness, review_scores_checkin, review_scores_communication, review_scores_location, review_scores_value) VALUES (%s, %s, %s, %s, %s, %s, %s, %s)(682651.0, 82.0, 9.0, 9.0, 9.0, 9.0, 9.0, 8.0)
INSERT INTO Listing_score(id, review_scores_rating, review_scores_accuracy, review_scores_cleanliness, review_scores_checkin, review_scores_communication, review_scores_location, review_scores_value) VALUES (%s, %s, %s, %s, %s, %s, %s, %s)(683208.0, 97.0, 10.0, 10.0, 10.0, 10.0, 10.0, 9.0)
INSERT INTO Listing_score(id, review_scores_rating, review_scores_accuracy, review_scores_cleanliness, review_scores_checkin, review_scores_communication, review_scores_location, review_scores_value) VALUES (%s, %s, %s, %s, %s, %s, %s, %s)(683401.0, 100.0, 10.0, 10.0, 10.0, 10.0, 10.0, 10.0)
INSERT INTO Listing_score(id, review_scores_rating, review_scores_accuracy, review_scores_cleanliness, review_scores_checkin, revi

In [40]:
att_columns = ['id', 'minimum_nights', 'maximum_nights', 'is_business_travel_ready', 'cancellation_policy', 'require_guest_profile_picture','require_guest_phone_verification']
insert_values(listings[att_columns], att_columns, "Listing_cond")

INSERT INTO Listing_cond(id, minimum_nights, maximum_nights, is_business_travel_ready, cancellation_policy, require_guest_profile_picture, require_guest_phone_verification) VALUES (%s, %s, %s, %s, %s, %s, %s)(18666, 3, 730, 'f', 'flexible', 'f', 'f')
INSERT INTO Listing_cond(id, minimum_nights, maximum_nights, is_business_travel_ready, cancellation_policy, require_guest_profile_picture, require_guest_phone_verification) VALUES (%s, %s, %s, %s, %s, %s, %s)(18674, 1, 1125, 'f', 'strict_14_with_grace_period', 'f', 'f')
INSERT INTO Listing_cond(id, minimum_nights, maximum_nights, is_business_travel_ready, cancellation_policy, require_guest_profile_picture, require_guest_phone_verification) VALUES (%s, %s, %s, %s, %s, %s, %s)(21605, 2, 1125, 'f', 'moderate', 'f', 'f')
INSERT INTO Listing_cond(id, minimum_nights, maximum_nights, is_business_travel_ready, cancellation_policy, require_guest_profile_picture, require_guest_phone_verification) VALUES (%s, %s, %s, %s, %s, %s, %s)(25786, 1, 730, 'f

In [61]:
att_columns = ['user_id', 'user_name']
insert_values(users[att_columns], att_columns, "Airbnb_user")

INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(1559265, 'Jody')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(4841196, 'Caron')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(11600277, 'Juan Carlos')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(35231385, 'Shlomi')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(23223644, 'Joost')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(4756672, 'Marius')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(57647372, 'Diane')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(62165990, 'Alejandro')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(67778905, 'Vladislava')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(64869468, 'Tania')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(19669204, 'Javier')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(59626397, 'Pavel')
INSERT INTO Airbnb_user(user_id, user_

INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(2041901, 'Dani')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(542867, 'Gabriela')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(1984642, 'Luciana')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(2074943, 'Kris')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(2108468, 'Carlotta')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(2116153, 'Victor/Paula')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(2142963, 'Igor')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(400416, 'Cens Sl')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(898600, 'Andre')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(2176121, 'Rosa María')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(2181314, 'Javier')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(2189222, 'Victor')
INSERT INTO Airbnb_user(user_id, user_name) VA

INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(4305310, 'Begoña')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(4235741, 'Carlos')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(4277536, 'Miguel')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(4159117, 'Raquel')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(4281126, 'Carmen')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(4453371, 'Maria')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(4286142, 'Juan & Ricardo')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(4292037, 'Miguel')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(4295642, 'Luisa')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(1341870, 'Charles')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(4084426, 'Agus')
INSERT INTO Airbnb_user(user_id, user_name) VALUES (%s, %s)(4211443, 'Amalia')
INSERT INTO Airbnb_user(user_id, user_name) VAL

In [64]:
att_columns = ['user_id', 'host_url', 'host_since', 'host_about', 'host_response_time', 'host_response_rate','host_thumbnail_url','host_picture_url','host_neighbourhood']
insert_values(listings[att_columns], att_columns, "Host")

INSERT INTO Host(user_id, host_url, host_since, host_about, host_response_time, host_response_rate, host_thumbnail_url, host_picture_url, host_neighbourhood) VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s)(71615, 'https://www.airbnb.com/users/show/71615', '2010-01-19', 'We are Mireia (39) & Maria (41), two multilingual entrepreneurs loving Barcelona and having big experience in the touristic market.\nIn our apartments you are going feel youself like at home. The location of our flats perfectly suites for travelling and sightseeing.\n\nWe are looking forward to sincerely host you in our apartments.\n', 'within an hour', '99%', 'https://a0.muscache.com/im/users/71615/profile_pic/1426612511/original.jpg?aki_policy=profile_small', 'https://a0.muscache.com/im/users/71615/profile_pic/1426612511/original.jpg?aki_policy=profile_x_medium', "El Camp de l'Arpa del Clot")
INSERT INTO Host(user_id, host_url, host_since, host_about, host_response_time, host_response_rate, host_thumbnail_url, host_pictur

INSERT INTO Host(user_id, host_url, host_since, host_about, host_response_time, host_response_rate, host_thumbnail_url, host_picture_url, host_neighbourhood) VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s)(4305310, 'https://www.airbnb.com/users/show/4305310', '2012-12-02', 'Hola soy de Madrid y me encanta mi ciudad.', 'within a few hours', '100%', 'https://a0.muscache.com/im/users/4305310/profile_pic/1354661181/original.jpg?aki_policy=profile_small', 'https://a0.muscache.com/im/users/4305310/profile_pic/1354661181/original.jpg?aki_policy=profile_x_medium', 'Palacio')
INSERT INTO Host(user_id, host_url, host_since, host_about, host_response_time, host_response_rate, host_thumbnail_url, host_picture_url, host_neighbourhood) VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s)(4235741, 'https://www.airbnb.com/users/show/4235741', '2012-11-25', nan, 'within an hour', '100%', 'https://a0.muscache.com/im/pictures/3fcbac15-b127-44ab-aae6-5d0394ce7743.jpg?aki_policy=profile_small', 'https://a0.muscache.com

In [66]:
att_columns = ['listing_id', 'id', 'user_id', 'date', 'comments']
insert_values(reviews[att_columns], att_columns, "Review")

INSERT INTO Review(listing_id, id, user_id, date, comments) VALUES (%s, %s, %s, %s, %s)(18666, 50158511, 1559265, '2015-10-10', 'Very nice flat. We had easy transportation to everywhere via the Metro. We could see Sagrada Familia from the terrace. Our hosts helped us with questions we had. Thanks!')
INSERT INTO Review(listing_id, id, user_id, date, comments) VALUES (%s, %s, %s, %s, %s)(18674, 4808211, 4841196, '2013-05-27', 'Great location. Clean, spacious flat. Would recommend to anyone.')
INSERT INTO Review(listing_id, id, user_id, date, comments) VALUES (%s, %s, %s, %s, %s)(18674, 10660311, 11600277, '2014-03-02', 'Mi mejor recomendación para este departamento. Cuida todos los detalles, adicionalmente muy cómodo, limpio, funcional y situado perfectamente. ')
INSERT INTO Review(listing_id, id, user_id, date, comments) VALUES (%s, %s, %s, %s, %s)(18674, 41087522, 35231385, '2015-08-04', 'Big apartment, well equipped.\nVery good service, excellent location.\nRecommended.')
INSERT INTO 

INSERT INTO Review(listing_id, id, user_id, date, comments) VALUES (%s, %s, %s, %s, %s)(30320, 35099578, 23890986, '2015-06-15', 'Lo consiguió porque el alojamiento tiene todo como para sentirte en casa. Se ha cuidado cada detalle para que así suceda . Además Dana y Mónica fueron excelentes anfitrionas y estuvieron atentas en cada momento para hacernos sentir, muy bien.')
INSERT INTO Review(listing_id, id, user_id, date, comments) VALUES (%s, %s, %s, %s, %s)(30320, 35513873, 27356093, '2015-06-19', 'Buena expereiencia. El depto está al lado de todo y ellos son muy amables y te ayudan en todo.')
INSERT INTO Review(listing_id, id, user_id, date, comments) VALUES (%s, %s, %s, %s, %s)(30320, 35702063, 27007125, '2015-06-21', "My friend and I stayed in Dana's apartment for a long weekend in Madrid. The apartment was exactly as described, small but spotlessly clean. The apartment is in a great location in the centre of the old Madrid. From here the Royal palace is a ten minute walk in one di

In [75]:
import mysql.connector
from mysql.connector import errorcode

try:
  cnx = mysql.connector.connect(
        host=HOST,
        port= PORT,
        user=USER,
        password=PASSWORD)
except mysql.connector.Error as err:
  if err.errno == errorcode.ER_ACCESS_DENIED_ERROR:
    print("Something is wrong with your user name or password")
  elif err.errno == errorcode.ER_BAD_DB_ERROR:
    print("Database does not exist")
  else:
    print(err)
else:
  cnx.close()

2013: Lost connection to MySQL server during query


In [74]:
import mysql.connector
from mysql.connector import Error
from mysql.connector import errorcode
try:
    connection = mysql.connector.connect(
        host=HOST,
        port= PORT,
        user=USER,
        password=PASSWORD)
    cursor = connection.cursor()
    cursor.execute("USE AIRBNB")
    cursor.execute("SELECT * FROM Listing")
finally:
    connection.close()

NameError: name 'connection' is not defined